In [1]:
from shapely.geometry import Point, Polygon
from datetime import datetime
import h3.api.numpy_int as h3
import pandas as pd
import geopandas as gpd
import numpy as np
import folium
import branca
from route3_client import Server


def dataframe_to_geodataframe(df: pd.DataFrame, column_name: str = "h3index") -> gpd.GeoDataFrame:
    return gpd.GeoDataFrame(df,
                            geometry=[Polygon(h3.h3_to_geo_boundary(h, geo_json=True)) for h in
                                      np.nditer(df[column_name].to_numpy())],
                            crs=4326)



In [2]:

disturbance = Point(10.86, 48.38).buffer(0.015)
target_points = [
    Point(10.903, 48.348263),
    Point(10.86698055267334, 48.465011068126444),
]

server = Server(hostport="127.0.0.1:7088")
t_start = datetime.now()
stats = server.analyze_disturbance_of_population_movement(
    disturbance, 
    10000.0, 
    target_points, 
    num_destinations_to_reach=3
)
print(f"took {datetime.now() - t_start}")
print(f"id: {stats.id}")
print(f"population within disturbance: {stats.population_within_disturbance}")
geo_df = dataframe_to_geodataframe(stats.dataframe, column_name="h3index_origin")
geo_df

took 0:00:15.973576
id: dec720ec-680d-4e63-a729-e1e9497f4c83
population within disturbance: 60158.96484375


h3index_origin  preferred_dest_h3index_without_disturbance  \
0     622051741058269183                                6.220519e+17   
1     622051741186228223                                6.220519e+17   
2     622051741454663679                                6.220519e+17   
3     622051849846947839                                6.220519e+17   
4     622051849755295743                                6.220519e+17   
...                  ...                                         ...   
6956  622051741214834687                                6.220519e+17   
6957  622051741051617279                                6.220519e+17   
6958  622051741744300031                                6.220518e+17   
6959  622051741755670527                                6.220519e+17   
6960  622051741723033599                                6.220518e+17   

      preferred_dest_h3index_with_disturbance  population_origin  \
0                                6.220518e+17          32.494858   
1                                6.220519e+17         238.423859   
2                                6.220519e+17         244.867752   
3                                6.220519e+17         109.546097   
4                                6.220519e+17         193.316650   
...                                       ...                ...   
6956                             6.220519e+17         148.209427   
6957                             6.220519e+17         107.233040   
6958                             6.220518e+17         110.482521   
6959                             6.220518e+17         154.653320   
6960                             6.220518e+17          45.123283   

      num_reached_without_disturbance  num_reached_with_disturbance  \
0                                   2                             2   
1                                   2                             2   
2                                   2                             2   
3                                   2                             2   
4                                   2                             2   
...                               ...                           ...   
6956                                2                             2   
6957                                2                             2   
6958                                2                             2   
6959                                2                             2   
6960                                2                             2   

      mean_cost_without_disturbance  mean_cost_with_disturbance  \
0                           18395.0                     23772.5   
1                           12072.0                     12072.0   
2                           33129.5                     40233.5   
3                           18673.5                     18673.5   
4                           18859.0                     18859.0   
...                             ...                         ...   
6956                        16290.5                     15737.0   
6957                        20979.5                     27735.5   
6958                        16697.5                     18706.0   
6959                        13203.5                     13841.0   
6960                         9365.5                      9365.5   

      cost_change_factor                                           geometry  
0               1.292335  POLYGON ((10.81780 48.38738, 10.81753 48.38674...  
1               1.000000  POLYGON ((10.88123 48.36364, 10.88096 48.36300...  
2               1.214431  POLYGON ((10.81906 48.32197, 10.81878 48.32133...  
3               1.000000  POLYGON ((10.91230 48.35132, 10.91203 48.35068...  
4               1.000000  POLYGON ((10.94047 48.35775, 10.94019 48.35710...  
...                  ...                                                ...  
6956            0.966023  POLYGON ((10.88452 48.34790, 10.88424 48.34726...  
6957            1.322029  POLYGON ((10.79713 4

In [4]:
map_center = geo_df.dissolve().centroid

m = folium.Map(location=[map_center.y, map_center.x], zoom_start=11, tiles='OpenStreetMap', 
               #crs="EPSG4326"
              )

colorscale_cell_worsen = branca.colormap.LinearColormap(((1.,1.,1.), (0.0,0.0,1.0)), vmin=1.0, vmax=geo_df['cost_change_factor'].max()) 
colorscale_cell_improve = branca.colormap.LinearColormap(((0.0,1.,0.0), (1.,1.,1.)), vmin=0.0, vmax=1.0) 
   
def style_cell(feature):
    cost_change = feature['properties']['cost_change_factor'] 
    if cost_change is None:
        fill = '#f00' # no route found
    elif cost_change > 1.0:
        fill = colorscale_cell_worsen(cost_change)
    else:
        fill = colorscale_cell_improve(cost_change)
    return {
        'fillColor': fill, 
        'color' : '#555',
        'weight' : 1,
        'fillOpacity' : 0.0 if cost_change == 1.0 else 0.8,
    }

folium.GeoJson(
    geo_df,
    style_function=style_cell,
    tooltip=folium.features.GeoJsonTooltip(["cost_change_factor", "population_origin"])
    ).add_to(m)    
    
m

/tmp/ipykernel_247290/2245090709.py:1: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  map_center = geo_df.dissolve().centroid
